In [1]:
import numpy as np
import pandas as pd
import matplotlib.pyplot as plt
from sklearn.metrics import r2_score,accuracy_score,f1_score

In [2]:
df = pd.read_csv('btc.csv')
df.head()

datetime      open      high       low     close      volume  \
0  2018-01-05 03:30:00  14797.89  14979.00  14601.00  14939.39  762.293702   
1  2018-01-05 04:30:00  14895.95  15100.08  14774.25  15059.54  892.734362   
2  2018-01-05 05:30:00  15059.56  15096.99  14802.00  14906.01  701.283048   
3  2018-01-05 06:30:00  14908.01  15100.00  14847.35  15040.00  922.722973   
4  2018-01-05 07:30:00  15038.04  15200.00  15038.04  15098.11  985.850712   

            ma7          ma21        rsi    upper_band  ...           sar  \
0  14765.905714  14693.307619  73.523748  15257.286699  ...  14099.125535   
1  14850.130000  14687.946667  74.235674  15234.686704  ...  14153.838003   
2  14886.861429  14678.190000  64.976108  15199.972788  ...  14229.537363   
3  14919.575714  14674.381905  65.475151  15183.639947  ...  14299.180774   
4  14948.564286  14685.001429  72.807464  15220.465386  ...  14363.252712   

          cci          vwap            efi         ema14         ema21  \
0   97.185359  14716.686419  107872.181770  14713.969375  14701.809507   
1  119.808224  14723.722367  107262.033594  14760.045459  14734.330461   
2   89.589687  14728.099258 -107667.986359  14779.507397  14749.937692   
3   95.183741  14735.202120  123635.651152  14814.239744  14776.306992   
4  119.877560  14745.591170   57287.784874  14852.089112  14805.561811   

         adx  diff_close  classi  Next_close  
0  46.365497      120.15       1    15059.54  
1  45.076379     -153.53       0    14906.01  
2  43.848079      133.99       1    15040.00  
3  42.071915       58.11       1    15098.11  
4  41.339725     -132.74       0    14965.37  

[5 rows x 28 columns]

In [3]:
df['Open'] = df['open']
df['Close'] = df['close']
df['High'] = df['high']
df['Low'] = df['low']
df['Volume'] = df['volume']

df.index = pd.to_datetime(df['datetime'])
df.drop(['open','high','low','close'], axis=1,inplace=True)

In [4]:
split_index = int(len(df) * 0.8)

first_80_percent = df.iloc[:split_index]
last_20_percent = df.iloc[split_index:]

In [5]:
X_train = first_80_percent[['Open', 'High', 'Low', 'Close', 'Volume', 'ma7', 'ma21',
       'rsi', 'upper_band', 'lower_band', 'ao', 'macd', 'signal_line',
       'choppiness_index', 'slowk', 'slowd', 'atr', 'sar', 'cci', 'vwap',
       'efi', 'ema14', 'ema21', 'adx']]
X_test = last_20_percent[['Open', 'High', 'Low', 'Close', 'Volume', 'ma7', 'ma21',
       'rsi', 'upper_band', 'lower_band', 'ao', 'macd', 'signal_line',
       'choppiness_index', 'slowk', 'slowd', 'atr', 'sar', 'cci', 'vwap',
       'efi', 'ema14', 'ema21', 'adx']]

In [6]:
y_class_train = first_80_percent['classi']
y_class_test = last_20_percent['classi']

In [7]:
y_reg_train = first_80_percent['Next_close']
y_reg_test = last_20_percent['Next_close']

In [8]:
from sklearn.ensemble import RandomForestClassifier

rfc_model = RandomForestClassifier(max_depth=5,
                                   min_samples_leaf=2,
                                   min_samples_split=10,
                                   random_state=42)
rfc_model.fit(X_train,y_class_train)
y_pred_m4 = rfc_model.predict(X_test)
accuracy_score(y_class_test,y_pred_m4)

0.5375966268446943

In [9]:
!pip install backtesting

In [23]:
from backtesting import Strategy
from backtesting.lib import crossover, TrailingStrategy

In [24]:
rfc_model.predict(X_test.iloc[-1:])

array([1], dtype=int64)

In [25]:
def PREDS_RFC(model,X):
  return pd.Series(model.predict(X))
def PREDS_XGB(model,X):
  return pd.Series(model.predict(X))
def time(X):
  return X.index

In [26]:
PREDS_RFC(rfc_model,X_test)

0       1
1       0
2       1
3       1
4       1
       ..
7110    1
7111    1
7112    1
7113    1
7114    1
Length: 7115, dtype: int64

In [27]:
time(X_test)

DatetimeIndex(['2021-04-09 08:30:00', '2021-04-09 09:30:00',
               '2021-04-09 10:30:00', '2021-04-09 11:30:00',
               '2021-04-09 12:30:00', '2021-04-09 13:30:00',
               '2021-04-09 14:30:00', '2021-04-09 15:30:00',
               '2021-04-09 16:30:00', '2021-04-09 17:30:00',
               ...
               '2022-01-30 20:30:00', '2022-01-30 21:30:00',
               '2022-01-30 22:30:00', '2022-01-30 23:30:00',
               '2022-01-31 00:30:00', '2022-01-31 01:30:00',
               '2022-01-31 02:30:00', '2022-01-31 03:30:00',
               '2022-01-31 04:30:00', '2022-01-31 05:30:00'],
              dtype='datetime64[ns]', name='datetime', length=7115, freq=None)

In [28]:
X = pd.concat([X_train,X_test])

In [29]:
def MACD(df,lb_fast,lb_slow,lb_sig):
  lb_fast = int(lb_fast)
  lb_slow = int(lb_slow)
  lb_sig = int(lb_sig)
  ema_fast = df['Close'].ewm(span=lb_fast).mean()
  ema_slow = df['Close'].ewm(span=lb_slow).mean()
  macd = ema_fast - ema_slow
  return np.array(macd)

def MACDSignal(df,lb_fast,lb_slow,lb_sig):
  lb_fast = int(lb_fast)
  lb_slow = int(lb_slow)
  lb_sig = int(lb_sig)
  ema_fast = df['Close'].ewm(span=lb_fast).mean()
  ema_slow = df['Close'].ewm(span=lb_slow).mean()
  macd = ema_fast - ema_slow
  signal = macd.ewm(span=lb_sig).mean()
  return np.array(signal)

def RSI(df, lb_r=14):
  lb_r = int(lb_r)
  delta = df['Close'].diff()

  gain = delta.where(delta > 0, 0)
  loss = -delta.where(delta < 0, 0)

  avg_gain = gain.rolling(window=lb_r, min_periods=1).mean()
  avg_loss = loss.rolling(window=lb_r, min_periods=1).mean()

  rs = avg_gain / avg_loss

  rsi = 100 - (100 / (1 + rs))

  return np.array(rsi)

def ATR(data, period=14):
    high = data['High']
    low = data['Low']
    close = data['Close']

    # Calculate True Range (TR)
    tr1 = high - low
    tr2 = abs(high - close.shift())
    tr3 = abs(low - close.shift())
    true_range = pd.concat([tr1, tr2, tr3], axis=1).max(axis=1)

    # Calculate ATR using Exponential Moving Average (EMA)
    atr = true_range.ewm(span=period, adjust=False).mean()

    return atr

In [185]:
def get_positions(X_test,rfc_model):
    preds = rfc_model.predict(X_test)
    close = np.array(X_test.Close)
    macd = MACD(X_test,lb_fast=82,lb_slow=40,lb_sig=16)
    signal = MACDSignal(X_test,lb_fast=82,lb_slow=40,lb_sig=16)
    rsi = RSI(X_test,lb_r=47)
    atr = ATR(X_test,period=14)
    rsi_top = 80.05
    rsi_bottom = 47.96
    tp = 4 
    sl = 4
    positions = [0]
    curr = 0
    in_price = -1

    for i in range(1,X_test.shape[0]):
        price = close[i]
        if preds[i]==1 and macd[i]>=signal[i] and macd[i-1]<=signal[i-1] and rsi[i]>=rsi_top:
           positions.append(1)
           in_price = price
           curr = 1
        elif preds[i]==0 and macd[i]<=signal[i] and macd[i-1]>=signal[i-1] and rsi[i]<=rsi_bottom:
            positions.append(-1)
            in_price = price
            curr = -1
        elif in_price>0 and curr==1 and (price-in_price > tp*atr[i] or in_price-price > sl*atr[i]):
            positions.append(-1)
            in_price=-1
        elif in_price>0 and curr==-1 and (price-in_price > sl*atr[i] or in_price-price > tp*atr[i]):
            positions.append(1)
            in_price=-1
        else:
            positions.append(0)
    return np.array(positions)

In [186]:
X_test.head()

Open      High       Low     Close       Volume  \
2021-04-09 08:30:00  57903.35  58167.76  57806.03  57985.71   979.303042   
2021-04-09 09:30:00  57985.71  58200.00  57971.06  58192.77  1219.538947   
2021-04-09 10:30:00  58192.76  58314.00  57947.66  57947.67  1277.356886   
2021-04-09 11:30:00  57947.67  58100.94  57809.38  57830.00  1445.825147   
2021-04-09 12:30:00  57830.81  58062.88  57654.00  58051.42  1704.039556   

                              ma7          ma21        rsi    upper_band  \
2021-04-09 08:30:00  57976.091429  57558.765238  64.442816  58580.391664   
2021-04-09 09:30:00  58050.815714  57614.339524  63.610411  58641.136329   
2021-04-09 10:30:00  58055.298571  57664.560000  54.447670  58645.317929   
2021-04-09 11:30:00  58019.938571  57719.500000  52.572033  58590.898601   
2021-04-09 12:30:00  57984.181429  57782.039524  56.615044  58538.550974   

                       lower_band  ...      slowk      slowd         atr  \
2021-04-09 08:30:00  56537.138812  ...  43.641685  61.916445  444.296358   
2021-04-09 09:30:00  56587.542718  ...  46.475532  50.540942  428.913761   
2021-04-09 10:30:00  56683.802071  ...  41.086490  43.734569  424.444207   
2021-04-09 11:30:00  56848.101399  ...  30.285175  39.282399  414.952478   
2021-04-09 12:30:00  57025.528073  ...  29.341383  33.571016  414.518729   

                              sar        cci          vwap            efi  \
2021-04-09 08:30:00  57542.445487  56.973688  13951.463160   80655.398539   
2021-04-09 09:30:00  57577.525667  99.915177  13952.320786  252517.734366   
2021-04-09 10:30:00  57611.202641  67.542075  13953.217988 -313080.172759   
2021-04-09 11:30:00  57643.532535  -5.770041  13954.229879 -170130.245047   
2021-04-09 12:30:00  58419.450000  -9.965382  13955.422679  377308.438490   

                            ema14         ema21        adx  
2021-04-09 08:30:00  57782.742710  57629.199695  46.268974  
2021-04-09 09:30:00  57837.413015  57680.433359  45.124089  
2021-04-09 10:30:00  57852.113946  57704.727599  44.576611  
2021-04-09 11:30:00  57849.165420  57716.115999  42.720023  
2021-04-09 12:30:00  57876.132697  57746.598181  41.009988  

[5 rows x 24 columns]

In [187]:
a = get_positions(X_test,rfc_model)
df = X_test[['Open','High','Low','Close','Volume']]

In [188]:
df['open'] = df['Open']
df['close'] = df['Close']
df['high'] = df['High']
df['low'] = df['Low']
df['volume'] = df['Volume']

df['datetime'] = df.index.astype('str')
df.drop(['Open','High','Low','Close','Volume'], axis=1,inplace=True)
df.head()

C:\Users\agnij\AppData\Local\Temp\ipykernel_15312\58455602.py:1: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df['open'] = df['Open']
C:\Users\agnij\AppData\Local\Temp\ipykernel_15312\58455602.py:2: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df['close'] = df['Close']
C:\Users\agnij\AppData\Local\Temp\ipykernel_15312\58455602.py:3: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the doc

open     close      high       low       volume  \
2021-04-09 08:30:00  57903.35  57985.71  58167.76  57806.03   979.303042   
2021-04-09 09:30:00  57985.71  58192.77  58200.00  57971.06  1219.538947   
2021-04-09 10:30:00  58192.76  57947.67  58314.00  57947.66  1277.356886   
2021-04-09 11:30:00  57947.67  57830.00  58100.94  57809.38  1445.825147   
2021-04-09 12:30:00  57830.81  58051.42  58062.88  57654.00  1704.039556   

                                datetime  
2021-04-09 08:30:00  2021-04-09 08:30:00  
2021-04-09 09:30:00  2021-04-09 09:30:00  
2021-04-09 10:30:00  2021-04-09 10:30:00  
2021-04-09 11:30:00  2021-04-09 11:30:00  
2021-04-09 12:30:00  2021-04-09 12:30:00

In [189]:
df.index = np.arange(X_test.shape[0])
df.head()

open     close      high       low       volume             datetime
0  57903.35  57985.71  58167.76  57806.03   979.303042  2021-04-09 08:30:00
1  57985.71  58192.77  58200.00  57971.06  1219.538947  2021-04-09 09:30:00
2  58192.76  57947.67  58314.00  57947.66  1277.356886  2021-04-09 10:30:00
3  57947.67  57830.00  58100.94  57809.38  1445.825147  2021-04-09 11:30:00
4  57830.81  58051.42  58062.88  57654.00  1704.039556  2021-04-09 12:30:00

In [190]:
df['signals']= a
df.head()

C:\Users\agnij\AppData\Local\Temp\ipykernel_15312\2054229982.py:1: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df['signals']= a


open     close      high       low       volume             datetime  \
0  57903.35  57985.71  58167.76  57806.03   979.303042  2021-04-09 08:30:00   
1  57985.71  58192.77  58200.00  57971.06  1219.538947  2021-04-09 09:30:00   
2  58192.76  57947.67  58314.00  57947.66  1277.356886  2021-04-09 10:30:00   
3  57947.67  57830.00  58100.94  57809.38  1445.825147  2021-04-09 11:30:00   
4  57830.81  58051.42  58062.88  57654.00  1704.039556  2021-04-09 12:30:00   

   signals  
0        0  
1        0  
2        0  
3        0  
4        0

In [191]:
df.signals.value_counts()

 0    7035
-1      44
 1      36
Name: signals, dtype: int64

In [192]:
df.to_csv('./signals.csv')

In [137]:
from backtesting import Backtest

bt_ = Backtest(X_test, Strat, cash=100_000, commission=0.0015)
stats = bt_.run()
stats

Start                     2021-04-09 08:30:00
End                       2022-01-31 05:30:00
Duration                    296 days 21:00:00
Exposure Time [%]                    28.29234
Equity Final [$]                 139865.84656
Equity Peak [$]                 188661.385085
Return [%]                          39.865847
Buy & Hold Return [%]              -36.485558
Return (Ann.) [%]                   50.824661
Volatility (Ann.) [%]               68.361588
Sharpe Ratio                         0.743468
Sortino Ratio                        1.884822
Calmar Ratio                         1.528226
Max. Drawdown [%]                  -33.257291
Avg. Drawdown [%]                   -3.235265
Max. Drawdown Duration      252 days 08:00:00
Avg. Drawdown Duration       10 days 00:00:00
# Trades                                   47
Win Rate [%]                        53.191489
Best Trade [%]                      14.744707
Worst Trade [%]                    -10.403974
Avg. Trade [%]                    

In [19]:
def PRICE(df):
    return df.Close

In [139]:
class MLStrategy(TrailingStrategy,Strategy):
  df = df
  model = rfc_model
  X = X_test
  lb_fast = 14
  lb_slow = 26
  lb_sig = 12
  lb_r = 14
  lb_atr = 14
  rsi_top = 50
  rsi_bottom = 50
  sl = 1
  tp = 2
  tsl = 6

  def init(self):
    super().init()
    self.forecasts1 = self.I(PREDS_RFC,self.model,self.X)
    self.forecasts2 = self.I(PREDS_XGB,self.model,self.X)
    self.price = self.I(PRICE,self.X)
    self.macd = self.I(MACD,self.X,self.lb_fast,self.lb_slow,self.lb_sig)
    self.signal = self.I(MACDSignal,self.X,self.lb_fast,self.lb_slow,self.lb_sig)
    self.rsi = self.I(RSI,self.X,self.lb_r)
    self.atr = self.I(ATR,self.X,self.lb_atr)

  def next(self):
    super().next()
    p = self.price[-1]
    atr = self.atr[-1]
    sl_ = int(self.sl)
    tp_ = int(self.tp)
    tsl_ = int(self.tsl)
    if self.forecasts1 > 0.5 and crossover(self.macd,self.signal) and self.rsi>self.rsi_top:
        self.position.close()
        self.buy(sl=p-sl_*atr, tp=p+tp_*atr)

    elif self.forecasts1 < 0.5 and crossover(self.signal,self.macd) and self.rsi<self.rsi_bottom:
        self.position.close()
        self.sell(sl=p+sl_*atr,tp=p-tp_*atr)

In [140]:
from backtesting import Backtest

bt = Backtest(X_test, MLStrategy, cash=100_000, commission=0.0015)
stats = bt.run()
stats

Start                     2021-04-09 08:30:00
End                       2022-01-31 05:30:00
Duration                    296 days 21:00:00
Exposure Time [%]                    3.078004
Equity Final [$]                100403.399152
Equity Peak [$]                 102221.836155
Return [%]                           0.403399
Buy & Hold Return [%]              -36.485558
Return (Ann.) [%]                     0.49432
Volatility (Ann.) [%]                8.987282
Sharpe Ratio                         0.055002
Sortino Ratio                        0.083464
Calmar Ratio                         0.040855
Max. Drawdown [%]                  -12.099309
Avg. Drawdown [%]                   -3.254009
Max. Drawdown Duration      262 days 10:00:00
Avg. Drawdown Duration       65 days 17:00:00
# Trades                                   25
Win Rate [%]                             40.0
Best Trade [%]                       4.022599
Worst Trade [%]                     -2.923134
Avg. Trade [%]                    

In [22]:
!pip install deap

In [26]:
import random
from deap import base, creator, tools, algorithms

creator.create('FitnessMulti', base.Fitness, weights=(1.0,2.0,1.0,1.0,2.0))
# (Maximize Win Rate [%], Maximize Return [%], Maximize Sharpe Ratio, Maximize # Trades, Maximize Max. Drawdown -> since we are taking it as -ve)
creator.create('Individual', list, fitness=creator.FitnessMulti)

In [27]:
toolbox = base.Toolbox()
toolbox.register('rand_lookb', random.randint, 1, 90) # for lookback, 150 ~ 24 * 7
toolbox.register('rand_pip', random.randint, 1, 10) # for tsl and tp
toolbox.register('rand_bottom', random.uniform,0,0.5) # for oversold RSI levels
toolbox.register('rand_top', random.uniform,0.5,1) # for overbought RSI levels

toolbox.register('individual', tools.initCycle, creator.Individual, (toolbox.rand_lookb,
                                                                     toolbox.rand_lookb,
                                                                     toolbox.rand_lookb,
                                                                     toolbox.rand_lookb,
                                                                     toolbox.rand_top,
                                                                     toolbox.rand_bottom,
                                                                     toolbox.rand_pip, # sl
                                                                     toolbox.rand_pip, # tp
                                                                     toolbox.rand_pip # tsl
                                                                    )
                                                                     ,n=1)

In [31]:
def evaluate(individual):
  stats = bt.optimize(lb_fast=[individual[0]],
                    lb_slow=[individual[1]],
                    lb_sig=[individual[2]],
                    lb_r = [individual[3]],
                    rsi_top = [100*individual[4]],
                    rsi_bottom = [100*individual[5]],
                    sl = [individual[6]],
                    tp = [individual[7]],
                    tsl = [individual[8]])
  return stats['Win Rate [%]'],stats['Return [%]'],stats['Sharpe Ratio'],stats['# Trades'],stats['Max. Drawdown [%]']

In [32]:
toolbox.register('evaluate', evaluate)
toolbox.register('mate', tools.cxSimulatedBinary, eta=20)
toolbox.register('mutate', tools.mutPolynomialBounded, low=1, up=300, eta=20, indpb=1.0/9)
toolbox.register('selectNSGA', tools.selNSGA2)
toolbox.register('selectSPEA', tools.selSPEA2)
toolbox.register('selectBest', tools.selBest)

In [33]:
toolbox.register("get", tools.initRepeat, list, toolbox.individual)

In [58]:
def feasible(individual):
  if(individual[0]<1 or individual[1]<1 or individual[2]<1 or individual[3]<1 or individual[6]<1 or 
     individual[6]>10 or individual[7]<1 or individual[7]>10 or individual[8]<1 or individual[8]>10 or individual[4]>1 or 
     individual[4]<0 or individual[5]>1 or individual[5]<0):
    return False
  stats = bt.optimize(lb_fast=[individual[0]],
                    lb_slow=[individual[1]],
                    lb_sig=[individual[2]],
                    lb_r = [individual[3]],
                    rsi_top = [individual[4]],
                    rsi_bottom = [individual[5]],
                    sl = [individual[6]],
                    tp = [individual[7]],
                    tsl = [individual[8]])
  if(stats['# Trades']<20):
    return False
  return True

In [59]:
x = toolbox.individual
x

functools.partial(<function initCycle at 0x000001F7EE94CEA0>, <class 'deap.creator.Individual'>, (functools.partial(<bound method Random.randint of <random.Random object at 0x000001F7DFF43F50>>, 1, 90), functools.partial(<bound method Random.randint of <random.Random object at 0x000001F7DFF43F50>>, 1, 90), functools.partial(<bound method Random.randint of <random.Random object at 0x000001F7DFF43F50>>, 1, 90), functools.partial(<bound method Random.randint of <random.Random object at 0x000001F7DFF43F50>>, 1, 90), functools.partial(<bound method Random.uniform of <random.Random object at 0x000001F7DFF43F50>>, 0.5, 1), functools.partial(<bound method Random.uniform of <random.Random object at 0x000001F7DFF43F50>>, 0, 0.5), functools.partial(<bound method Random.randint of <random.Random object at 0x000001F7DFF43F50>>, 1, 10), functools.partial(<bound method Random.randint of <random.Random object at 0x000001F7DFF43F50>>, 1, 10), functools.partial(<bound method Random.randint of <random.Ra

In [60]:
# Create the initial population
# population = toolbox.population(n=100)
from tqdm.auto import tqdm

population = []
for i in tqdm(range(200)):
    individual = toolbox.get(n=1)
    if(feasible(individual[0])):
        population.append(individual[0])
                         

# Evaluate the entire population
fitnesses = list(map(toolbox.evaluate, population))
for ind, fit in zip(population, fitnesses):
    ind.fitness.values = fit

  0%|          | 0/200 [00:00<?, ?it/s]

  0%|          | 0/1 [00:00<?, ?it/s]

  0%|          | 0/1 [00:00<?, ?it/s]

  0%|          | 0/1 [00:00<?, ?it/s]

  0%|          | 0/1 [00:00<?, ?it/s]

...

  0%|          | 0/1 [00:00<?, ?it/s]

  0%|          | 0/1 [00:00<?, ?it/s]

  0%|          | 0/1 [00:00<?, ?it/s]

  0%|          | 0/1 [00:00<?, ?it/s]

  0%|          | 0/1 [00:00<?, ?it/s]

In [61]:
len(population)

149

In [63]:
fronts_initial = tools.sortNondominated(population, len(population), first_front_only=True)[0]
for i, ind in enumerate(fronts_initial):
    print(f'Individual {i + 1}')
    print('************************')
    print(f'Individual: {ind}')
    print(f'Objectives: {ind.fitness.values}')

Individual 1
************************
Individual: [15, 2, 44, 29, 0.6102218547611191, 0.32370873878092316, 9, 1, 5]
Objectives: (86.11111111111111, 15.304764243321625, 1.0168321533287974, 72.0, -9.495312610315398)
Individual 2
************************
Individual: [16, 31, 51, 9, 0.7634268508209264, 0.11149068225675024, 8, 5, 5]
Objectives: (100.0, 5.530307877653278, 1.4863975742729671, 1.0, -0.603704193231358)
Individual 3
************************
Individual: [5, 75, 41, 25, 0.5986033856810855, 0.28107785705080707, 7, 1, 6]
Objectives: (100.0, 2.745956168404271, 0.4850889670251885, 3.0, -5.210290000000006)
Individual 4
************************
Individual: [90, 7, 74, 24, 0.6732489784617319, 0.11176130545043417, 10, 1, 9]
Objectives: (100.0, 0.7290911114025512, 1.5320096640951324, 1.0, -0.0)
Individual 5
************************
Individual: [24, 83, 14, 3, 0.7059736832393211, 0.3048342180290911, 4, 5, 1]
Objectives: (32.0, -2.016036220000009, 0.0, 25.0, -7.395382732979372)
Individual 6


In [64]:
import warnings
warnings.filterwarnings("ignore")
from tqdm.auto import tqdm
pop = population.copy()
# Configure the algorithm
NGEN = 100
MU = 40
LAMBDA = 500
CXPB = 0.9
MUTPB = 1.0/len(population)

for g in tqdm(range(NGEN)):
    print('Generation: ',g)
    # Select the next generation individuals
    population1 = toolbox.selectNSGA(population,MU)
    population2 = toolbox.selectSPEA(population,MU)
    population = population1+population2

    offspring = algorithms.varAnd(population,toolbox,cxpb=CXPB,mutpb=MUTPB)

    # Evaluate the individuals with an invalid fitness
    offspring = list(filter(feasible,offspring))
    if(len(offspring)<100):
        offspring+=population[:100-len(offspring)]
    invalid_ind = [ind for ind in offspring if not ind.fitness.valid]
    fitnesses = toolbox.map(toolbox.evaluate, invalid_ind)
    for ind, fit in zip(invalid_ind, fitnesses):
        ind.fitness.values = fit

    # The population is entirely replaced by the offspring
    population = toolbox.selectBest(offspring,100,fit_attr='fitness')

  0%|          | 0/100 [00:00<?, ?it/s]

Generation:  0


  0%|          | 0/1 [00:00<?, ?it/s]

  0%|          | 0/1 [00:00<?, ?it/s]

  0%|          | 0/1 [00:00<?, ?it/s]

...

  0%|          | 0/1 [00:00<?, ?it/s]

  0%|          | 0/1 [00:00<?, ?it/s]

  0%|          | 0/1 [00:00<?, ?it/s]

  0%|          | 0/1 [00:00<?, ?it/s]

  0%|          | 0/1 [00:00<?, ?it/s]

In [65]:
fronts_final = tools.sortNondominated(population, len(population), first_front_only=True)[0]
for i, ind in enumerate(fronts_final):
    print(f"Individual {i + 1} - Objectives: {ind.fitness.values}")

Individual 1 - Objectives: (100.0, 13.430676864663635, 3.1350556128520255, 14.0, -1.6551074574895797)
Individual 2 - Objectives: (100.0, 13.430676864663635, 3.1350556128520255, 14.0, -1.6551074574895797)
Individual 3 - Objectives: (100.0, 11.052899781158107, 3.6235913951190453, 13.0, -1.3791870986957555)
Individual 4 - Objectives: (100.0, 0.7290911114025512, 1.5320096640951324, 1.0, -0.0)
Individual 5 - Objectives: (100.0, 0.7290911114025512, 1.5320096640951324, 1.0, -0.0)
Individual 6 - Objectives: (100.0, 0.7290911114025512, 1.5320096640951324, 1.0, -0.0)
Individual 7 - Objectives: (100.0, 0.7290911114025512, 1.5320096640951324, 1.0, -0.0)
Individual 8 - Objectives: (93.33333333333333, 12.7662990535274, 2.87717081469573, 15.0, -1.672365132063447)
Individual 9 - Objectives: (93.18181818181817, 13.11701662571747, 0.9324382261647256, 44.0, -11.800723706288318)
Individual 10 - Objectives: (92.5925925925926, 23.0490448425754, 1.5854243357402453, 54.0, -10.621307810300207)
Individual 11 - 

In [66]:
for i, ind in enumerate(fronts_final):
    print(f"Individual {i + 1} : {ind}")

Individual 1 : [60.701128909635536, 71.8030048046417, 48.031015350502884, 2.6358906396112483, 0.9251298218301587, 0.10170003871278996, 2.6985567778167643, 1.4504705388495824, 5.07217289849307]
Individual 2 : [60.701128909635536, 71.8030048046417, 48.031015350502884, 2.6358906396112483, 0.9251298218301587, 0.10170003871278996, 2.6985567778167643, 1.4504705388495824, 5.07217289849307]
Individual 3 : [60.068777424880665, 70.75814498710743, 48.070208319959924, 2.9009111295363974, 0.94742925381598, 0.09378304945824797, 3.578734640098617, 1.3832884461091504, 4.576598842762296]
Individual 4 : [89.47534477560961, 6.70066425350408, 72.69895595426905, 24.28180339191614, 0.6726287833917851, 0.11259025924535368, 9.85710188531793, 1.1019544004486117, 9.386855781172041]
Individual 5 : [89.16019867529059, 6.151261546087947, 74.79911854753111, 23.970947116085007, 0.6802052974402749, 0.11195028599381836, 9.96482914741625, 1.0863592664904849, 9.066884582212266]
Individual 6 : [89.16111807020123, 6.14001

In [142]:
stats = bt.optimize(lb_fast=[82],
                    lb_slow=[40],
                    lb_sig=[16],
                    lb_r = [47],
                    rsi_top = [100*0.8005],
                    rsi_bottom = [100*0.4796],
                    sl = 4,
                    tp= 4,
                    tsl = 6)
stats

  0%|          | 0/1 [00:00<?, ?it/s]

Start                     2021-04-09 08:30:00
End                       2022-01-31 05:30:00
Duration                    296 days 21:00:00
Exposure Time [%]                   23.148278
Equity Final [$]                220977.286369
Equity Peak [$]                 227206.186369
Return [%]                         120.977286
Buy & Hold Return [%]              -36.485558
Return (Ann.) [%]                  164.099803
Volatility (Ann.) [%]               94.008247
Sharpe Ratio                         1.745589
Sortino Ratio                        8.692681
Calmar Ratio                          9.52136
Max. Drawdown [%]                  -17.234912
Avg. Drawdown [%]                   -2.252963
Max. Drawdown Duration       90 days 04:00:00
Avg. Drawdown Duration        3 days 09:00:00
# Trades                                   44
Win Rate [%]                             75.0
Best Trade [%]                      12.458878
Worst Trade [%]                    -13.410933
Avg. Trade [%]                    

In [2]:
bt.plot().show()

NameError: name 'bt' is not defined